In [218]:
import pyodbc
import pandas as pd
import difflib
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

In [219]:
server = 'dataintegrationproject.database.windows.net' 
database = 'DieZweiFragezeichen' 
username = 'di_public' 
password = 'DI_Pub2022!'  
cnxn = pyodbc.connect('DRIVER={SQL Server};SERVER='+server+';DATABASE='+database+';UID='+username+';PWD='+ password)
cursor = cnxn.cursor()

In [220]:
q_HDI = "SELECT * FROM HDI;"
q_AdjustedNI = "SELECT * FROM AdjustedNetIncome;"
q_Countries = "SELECT * FROM Countries;"
q_CountryGdp = "SELECT * FROM CountryGdp;"
q_DurSchoolCompulsory = "SELECT * FROM DurSchoolCompulsory;"
q_LifeExpectancy = "SELECT * FROM LifeExpectancy;"
q_LiteracyRate = "SELECT * FROM LiteracyRate;"

HDI = pd.read_sql(q_HDI, cnxn)
AdjustedNetIncome = pd.read_sql(q_AdjustedNI, cnxn)
Countries = pd.read_sql(q_Countries, cnxn)
CountryGdp = pd.read_sql(q_CountryGdp, cnxn)
DurSchoolCompulsory = pd.read_sql(q_DurSchoolCompulsory, cnxn)
LifeExpectancy = pd.read_sql(q_LifeExpectancy, cnxn)
LiteracyRate = pd.read_sql(q_LiteracyRate, cnxn)

In [221]:
CountryGdp

Country Name Country Code     Indicator Name  \
0                          Aruba          ABW  GDP (current US$)   
1    Africa Eastern and Southern          AFE  GDP (current US$)   
2                    Afghanistan          AFG  GDP (current US$)   
3     Africa Western and Central          AFW  GDP (current US$)   
4                         Angola          AGO  GDP (current US$)   
..                           ...          ...                ...   
261                       Kosovo          XKX  GDP (current US$)   
262                  Yemen, Rep.          YEM  GDP (current US$)   
263                 South Africa          ZAF  GDP (current US$)   
264                       Zambia          ZMB  GDP (current US$)   
265                     Zimbabwe          ZWE  GDP (current US$)   

     Indicator Code          1960          1961          1962          1963  \
0    NY.GDP.MKTP.CD           NaN           NaN           NaN           NaN   
1    NY.GDP.MKTP.CD  2.008272e+10  2.050945e+10  2.235043e+10  2.675866e+10   
2    NY.GDP.MKTP.CD  5.377778e+08  5.488889e+08  5.466667e+08  7.511112e+08   
3    NY.GDP.MKTP.CD  1.040428e+10  1.112805e+10  1.194335e+10  1.267652e+10   
4    NY.GDP.MKTP.CD           NaN           NaN           NaN           NaN   
..              ...           ...           ...           ...           ...   
261  NY.GDP.MKTP.CD           NaN           NaN           NaN           NaN   
262  NY.GDP.MKTP.CD           NaN           NaN           NaN           NaN   
263  NY.GDP.MKTP.CD  7.575397e+09  7.972997e+09  8.497997e+09  9.423396e+09   
264  NY.GDP.MKTP.CD  7.130000e+08  6.962857e+08  6.931429e+08  7.187143e+08   
265  NY.GDP.MKTP.CD  1.052990e+09  1.096647e+09  1.117602e+09  1.159512e+09   

             1964          1965  ...          2012          2013  \
0             NaN           NaN  ...  2.534637e+09  2.727850e+09   
1    2.446499e+10  2.787894e+10  ...  9.505214e+11  9.642424e+11   
2    8.000000e+08  1.006667e+09  ...  1.990732e+10  2.014640e+10   
3    1.383858e+10  1.486247e+10  ...  7.275714e+11  8.207876e+11   
4             NaN           NaN  ...  1.280529e+11  1.367099e+11   
..            ...           ...  ...           ...           ...   
261           NaN           NaN  ...  6.163785e+09  6.735731e+09   
262           NaN           NaN  ...  3.540134e+10  4.041524e+10   
263  1.037400e+10  1.133440e+10  ...  4.344005e+11  4.008860e+11   
264  8.394286e+08  1.082857e+09  ...  2.550306e+10  2.803724e+10   
265  1.217138e+09  1.311436e+09  ...  1.711485e+10  1.909102e+10   

             2014          2015          2016          2017          2018  \
0    2.790849e+09  2.962905e+09  2.983637e+09  3.092430e+09  3.202189e+09   
1    9.848071e+11  9.199300e+11  8.733549e+11  9.853557e+11  1.012853e+12   
2    2.049713e+10  1.913421e+10  1.811656e+10  1.875347e+10  1.805323e+10   
3    8.649666e+11  7.607297e+11  6.905430e+11  6.837416e+11  7.416916e+11   
4    1.457122e+11  1.161936e+11  1.011239e+11  1.221238e+11  1.013532e+11   
..            ...           ...           ...           ...           ...   
261  7.074658e+09  6.295820e+09  6.682833e+09  7.180813e+09  7.878509e+09   
262  4.322859e+10  4.244510e+10  3.131737e+10  2.684013e+10  2.160614e+10   
263  3.811989e+11  3.467098e+11  3.235855e+11  3.814488e+11  4.048421e+11   
264  2.714102e+10  2.125122e+10  2.095841e+10  2.587360e+10  2.631159e+10   
265  1.949552e+10  1.996312e+10  2.054868e+10  1.758489e+10  1.811554e+10   

             2019          2020  2021  
0             NaN           NaN  None  
1    1.009910e+12  9.207923e+11  None  
2    1.879945e+10  2.011614e+10  None  
3    7.945725e+11  7.845876e+11  None  
4    8.941719e+10  5.837598e+10  None  
..            ...           ...   ...  
261  7.899879e+09  7.716925e+09  None  
262           NaN           NaN  None  
263  3.879346e+11  3.354421e+11  None  
264  2.330867e+10  1.811063e+10  None  
265  1.928429e+10  1.805117e+10  None  

[266 rows x 66 columns]

In [222]:
HDI['Country1'] = HDI['Country'].apply(lambda x: difflib.get_close_matches(x, Countries['TableName']))
HDI['Country1'] = HDI['Country1'].str[0]
HDI

HDI Rank                             Country   1990   1991   1992   1993  \
0        169                         Afghanistan  0.302  0.307  0.316  0.312   
1         69                             Albania   0.65  0.631  0.615  0.618   
2         91                             Algeria  0.572  0.576  0.582  0.586   
3         36                             Andorra     ..     ..     ..     ..   
4        148                              Angola     ..     ..     ..     ..   
..       ...                                 ...    ...    ...    ...    ...   
184      113  Venezuela (Bolivarian Republic of)  0.644  0.654   0.66  0.662   
185      117                            Viet Nam  0.483  0.493  0.504  0.514   
186      179                               Yemen  0.401  0.401  0.404  0.406   
187      146                              Zambia  0.421  0.417  0.416  0.419   
188      150                            Zimbabwe  0.478  0.481  0.467  0.463   

      1994   1995   1996   1997  ...   2011   2012   2013   2014   2015  \
0    0.307  0.331  0.335  0.339  ...  0.477  0.489  0.496    0.5    0.5   
1    0.624  0.637  0.646  0.645  ...  0.764  0.775  0.782  0.787  0.788   
2     0.59  0.595  0.602  0.611  ...  0.728  0.728  0.729  0.736   0.74   
3       ..     ..     ..     ..  ...  0.836  0.858  0.856  0.863  0.862   
4       ..     ..     ..     ..  ...  0.533  0.544  0.555  0.565  0.572   
..     ...    ...    ...    ...  ...    ...    ...    ...    ...    ...   
184  0.662  0.666  0.668   0.67  ...  0.769  0.772  0.777  0.775  0.769   
185  0.525  0.537  0.548  0.547  ...  0.671  0.676  0.681  0.683  0.688   
186  0.408  0.414  0.421  0.426  ...  0.506  0.504  0.509  0.502  0.483   
187  0.414  0.415  0.416  0.416  ...  0.534  0.549  0.557  0.561  0.569   
188   0.46  0.453  0.453  0.447  ...  0.499  0.525  0.537  0.547  0.553   

      2016   2017   2018   2019     Country1  
0    0.502  0.506  0.509  0.511  Afghanistan  
1    0.788   0.79  0.792  0.795      Albania  
2    0.743  0.745  0.746  0.748      Algeria  
3    0.866  0.863  0.867  0.868      Andorra  
4    0.578  0.582  0.582  0.581       Angola  
..     ...    ...    ...    ...          ...  
184  0.759  0.743  0.733  0.711          NaN  
185  0.693  0.696    0.7  0.704      Vietnam  
186  0.474  0.467  0.468   0.47  Yemen, Rep.  
187  0.571  0.578  0.582  0.584       Zambia  
188  0.558  0.563  0.569  0.571     Zimbabwe  

[189 rows x 33 columns]

In [223]:
HDI.to_excel(r"HDI_update.xlsx")

In [224]:
def fuzzy_merge(df_1, df_2, key1, key2, threshold=90, limit=1):
    """
    :param df_1: the left table to join
    :param df_2: the right table to join
    :param key1: key column of the left table
    :param key2: key column of the right table
    :param threshold: how close the matches should be to return a match, based on Levenshtein distance
    :param limit: the amount of matches that will get returned, these are sorted high to low
    :return: dataframe with boths keys and matches
    """
    s = df_2[key2].tolist()
    
    m = df_1[key1].apply(lambda x: process.extract(x, s, limit=limit))    
    df_1['matches'] = m
    
    m2 = df_1['matches'].apply(lambda x: ', '.join([i[0] for i in x if i[1] >= threshold]))
    df_1['matches'] = m2
    
    return df_1

In [225]:
HDI_fuzzy = fuzzy_merge(HDI, Countries, 'Country', 'TableName', threshold=80)

In [226]:
HDI_fuzzy.to_excel(r"HDI_fuzzy.xlsx") 

In [227]:
HDI_update = pd.merge(HDI_fuzzy,Countries[["TableName","Country Code"]],how='left',left_on='matches',right_on='TableName')

In [228]:
HDI_update.loc[(HDI_update.Country == 'Czechia'),"Country Code"] = 'CZE'
HDI_update.loc[(HDI_update.Country == 'Kyrgyzstan'),"Country Code"] = 'KGZ'
HDI_update.loc[(HDI_update.Country == "Lao People's Democratic Republic"),"Country Code"] = 'LAO'
HDI_update.loc[(HDI_update.Country == '"Palestine'),"Country Code"] = 'PSE'
HDI_update.loc[(HDI_update.Country == 'Slovakia'),"Country Code"] = 'SVK'
HDI_update.loc[(HDI_update.Country == 'Venezuela (Bolivarian Republic of)'),"Country Code"] = 'VEN'

In [229]:
HDI_update.loc[(HDI_update.Country == 'Czechia')]
HDI_update.loc[(HDI_update.Country == 'Venezuela (Bolivarian Republic of)')]

HDI Rank                             Country   1990   1991  1992   1993  \
184      113  Venezuela (Bolivarian Republic of)  0.644  0.654  0.66  0.662   

      1994   1995   1996  1997  ...   2014   2015   2016   2017   2018   2019  \
184  0.662  0.666  0.668  0.67  ...  0.775  0.769  0.759  0.743  0.733  0.711   

    Country1         matches       TableName Country Code  
184      NaN  Czech Republic  Czech Republic          VEN  

[1 rows x 36 columns]

In [230]:
HDI_update1 = HDI_update[['Country Code', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019']]
HDI = HDI_update1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
HDI

Country Code  Year  Value
0             AFG  1990  0.302
1             ALB  1990   0.65
2             DZA  1990  0.572
3             AND  1990     ..
4             AGO  1990     ..
...           ...   ...    ...
5665          VEN  2019  0.711
5666          VNM  2019  0.704
5667          YEM  2019   0.47
5668          ZMB  2019  0.584
5669          ZWE  2019  0.571

[5670 rows x 3 columns]

In [231]:
HDI.drop(HDI[HDI['Value'] == '..'].index, inplace = True)
HDI['Table'] = 'HDI'
HDI

Country Code  Year  Value Table
0             AFG  1990  0.302   HDI
1             ALB  1990   0.65   HDI
2             DZA  1990  0.572   HDI
6             ARG  1990  0.718   HDI
7             ARM  1990  0.654   HDI
...           ...   ...    ...   ...
5665          VEN  2019  0.711   HDI
5666          VNM  2019  0.704   HDI
5667          YEM  2019   0.47   HDI
5668          ZMB  2019  0.584   HDI
5669          ZWE  2019  0.571   HDI

[5153 rows x 4 columns]

In [232]:
AdjustedNetIncome1 = AdjustedNetIncome[['Country Code','1960','1961','1962','1963','1964','1965','1966','1967','1968','1969','1970','1971','1972','1973','1974','1975','1976','1977','1978','1979','1980','1981','1982','1983','1984','1985','1986','1987','1988','1989', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019','2020','2021']]
AdjustedNetIncome1 = AdjustedNetIncome1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
AdjustedNetIncome1['Table'] = 'AdjustedNetIncome'
AdjustedNetIncome1

Country Code  Year Value              Table
0              ABW  1960  None  AdjustedNetIncome
1              AFE  1960  None  AdjustedNetIncome
2              AFG  1960  None  AdjustedNetIncome
3              AFW  1960  None  AdjustedNetIncome
4              AGO  1960  None  AdjustedNetIncome
...            ...   ...   ...                ...
16487          XKX  2021  None  AdjustedNetIncome
16488          YEM  2021  None  AdjustedNetIncome
16489          ZAF  2021  None  AdjustedNetIncome
16490          ZMB  2021  None  AdjustedNetIncome
16491          ZWE  2021  None  AdjustedNetIncome

[16492 rows x 4 columns]

In [233]:
AdjustedNetIncome2 = AdjustedNetIncome1.dropna()
AdjustedNetIncome2

Country Code  Year        Value              Table
2662           AFG  1970   148.531898  AdjustedNetIncome
2663           AFW  1970   195.501526  AdjustedNetIncome
2669           ARG  1970   1194.69568  AdjustedNetIncome
2673           AUS  1970  2679.493439  AdjustedNetIncome
2674           AUT  1970  1759.625085  AdjustedNetIncome
...            ...   ...          ...                ...
16219          WLD  2020  8767.399212  AdjustedNetIncome
16220          WSM  2020  3465.005406  AdjustedNetIncome
16223          ZAF  2020  4548.301112  AdjustedNetIncome
16224          ZMB  2020   712.741793  AdjustedNetIncome
16225          ZWE  2020   940.371947  AdjustedNetIncome

[9337 rows x 4 columns]

In [234]:
CountryGdp1 = CountryGdp[['Country Code','1960','1961','1962','1963','1964','1965','1966','1967','1968','1969','1970','1971','1972','1973','1974','1975','1976','1977','1978','1979','1980','1981','1982','1983','1984','1985','1986','1987','1988','1989', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019','2020','2021']]
CountryGdp1 = CountryGdp1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
CountryGdp1['Table'] = 'CountryGdp'
CountryGdp1

Country Code  Year               Value       Table
0              ABW  1960                 NaN  CountryGdp
1              AFE  1960  20082715853.689075  CountryGdp
2              AFG  1960    537777811.111111  CountryGdp
3              AFW  1960  10404280784.153095  CountryGdp
4              AGO  1960                 NaN  CountryGdp
...            ...   ...                 ...         ...
16487          XKX  2021                None  CountryGdp
16488          YEM  2021                None  CountryGdp
16489          ZAF  2021                None  CountryGdp
16490          ZMB  2021                None  CountryGdp
16491          ZWE  2021                None  CountryGdp

[16492 rows x 4 columns]

In [235]:
CountryGdp2 = CountryGdp1.dropna()
CountryGdp2

Country Code  Year                Value       Table
1              AFE  1960   20082715853.689075  CountryGdp
2              AFG  1960     537777811.111111  CountryGdp
3              AFW  1960   10404280784.153095  CountryGdp
13             AUS  1960   18606786874.230038  CountryGdp
14             AUT  1960     6592693841.18495  CountryGdp
...            ...   ...                  ...         ...
16220          WSM  2020     807100820.648132  CountryGdp
16221          XKX  2020    7716925356.125357  CountryGdp
16223          ZAF  2020  335442101366.417358  CountryGdp
16224          ZMB  2020    18110631358.31139  CountryGdp
16225          ZWE  2020   18051170798.941048  CountryGdp

[12854 rows x 4 columns]

In [236]:
DurSchoolCompulsory1 = DurSchoolCompulsory[['Country Code','1960','1961','1962','1963','1964','1965','1966','1967','1968','1969','1970','1971','1972','1973','1974','1975','1976','1977','1978','1979','1980','1981','1982','1983','1984','1985','1986','1987','1988','1989', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019','2020','2021']]
DurSchoolCompulsory1 = DurSchoolCompulsory1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
DurSchoolCompulsory1['Table'] = 'DurSchoolCompulsory'
DurSchoolCompulsory1

Country Code  Year Value                Table
0              ABW  1960  None  DurSchoolCompulsory
1              AFE  1960  None  DurSchoolCompulsory
2              AFG  1960  None  DurSchoolCompulsory
3              AFW  1960  None  DurSchoolCompulsory
4              AGO  1960  None  DurSchoolCompulsory
...            ...   ...   ...                  ...
16487          XKX  2021   NaN  DurSchoolCompulsory
16488          YEM  2021   NaN  DurSchoolCompulsory
16489          ZAF  2021   NaN  DurSchoolCompulsory
16490          ZMB  2021   NaN  DurSchoolCompulsory
16491          ZWE  2021   NaN  DurSchoolCompulsory

[16492 rows x 4 columns]

In [237]:
DurSchoolCompulsory2 = DurSchoolCompulsory1.dropna()
DurSchoolCompulsory2

Country Code  Year Value                Table
10109          AFE  1998   7.0  DurSchoolCompulsory
10110          AFG  1998   6.0  DurSchoolCompulsory
10111          AFW  1998   9.0  DurSchoolCompulsory
10112          AGO  1998   4.0  DurSchoolCompulsory
10113          ALB  1998   8.0  DurSchoolCompulsory
...            ...   ...   ...                  ...
16460          TJK  2021   9.0  DurSchoolCompulsory
16461          TKM  2021  12.0  DurSchoolCompulsory
16477          USA  2021  12.0  DurSchoolCompulsory
16478          UZB  2021  12.0  DurSchoolCompulsory
16481          VGB  2021  12.0  DurSchoolCompulsory

[5360 rows x 4 columns]

In [238]:
LifeExpectancy1 = LifeExpectancy[['Country Code','1960','1961','1962','1963','1964','1965','1966','1967','1968','1969','1970','1971','1972','1973','1974','1975','1976','1977','1978','1979','1980','1981','1982','1983','1984','1985','1986','1987','1988','1989', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019','2020','2021']]
LifeExpectancy1 = LifeExpectancy1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
LifeExpectancy1['Table'] = 'LifeExpectancy'
LifeExpectancy1

Country Code  Year      Value           Table
0              ABW  1960     65.662  LifeExpectancy
1              AFE  1960  42.716053  LifeExpectancy
2              AFG  1960     32.446  LifeExpectancy
3              AFW  1960   37.20538  LifeExpectancy
4              AGO  1960     37.524  LifeExpectancy
...            ...   ...        ...             ...
16487          XKX  2021       None  LifeExpectancy
16488          YEM  2021       None  LifeExpectancy
16489          ZAF  2021       None  LifeExpectancy
16490          ZMB  2021       None  LifeExpectancy
16491          ZWE  2021       None  LifeExpectancy

[16492 rows x 4 columns]

In [239]:
LifeExpectancy2 = LifeExpectancy1.dropna()
LifeExpectancy2

Country Code  Year      Value           Table
0              ABW  1960     65.662  LifeExpectancy
1              AFE  1960  42.716053  LifeExpectancy
2              AFG  1960     32.446  LifeExpectancy
3              AFW  1960   37.20538  LifeExpectancy
4              AGO  1960     37.524  LifeExpectancy
...            ...   ...        ...             ...
16221          XKX  2020  71.087805  LifeExpectancy
16222          YEM  2020     66.181  LifeExpectancy
16223          ZAF  2020     64.379  LifeExpectancy
16224          ZMB  2020     64.194  LifeExpectancy
16225          ZWE  2020     61.738  LifeExpectancy

[14858 rows x 4 columns]

In [240]:
LiteracyRate1 = LiteracyRate[['Country Code','1960','1961','1962','1963','1964','1965','1966','1967','1968','1969','1970','1971','1972','1973','1974','1975','1976','1977','1978','1979','1980','1981','1982','1983','1984','1985','1986','1987','1988','1989', '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019','2020','2021']]
LiteracyRate1 = LiteracyRate1.melt(id_vars=["Country Code"], 
        var_name="Year", 
        value_name="Value")
LiteracyRate1['Table'] = 'LiteracyRate'
LiteracyRate1

Country Code  Year Value         Table
0              ABW  1960  None  LiteracyRate
1              AFE  1960  None  LiteracyRate
2              AFG  1960  None  LiteracyRate
3              AFW  1960  None  LiteracyRate
4              AGO  1960  None  LiteracyRate
...            ...   ...   ...           ...
16487          XKX  2021   NaN  LiteracyRate
16488          YEM  2021   NaN  LiteracyRate
16489          ZAF  2021   NaN  LiteracyRate
16490          ZMB  2021   NaN  LiteracyRate
16491          ZWE  2021   NaN  LiteracyRate

[16492 rows x 4 columns]

In [241]:
LiteracyRate2 = LiteracyRate1.dropna()
LiteracyRate2

Country Code  Year      Value         Table
4529           ARB  1977  44.902969  LiteracyRate
4583           EAP  1977   63.98658  LiteracyRate
4584           EAR  1977  49.721581  LiteracyRate
4585           EAS  1977   66.13179  LiteracyRate
4624           IBD  1977  63.442829  LiteracyRate
...            ...   ...        ...           ...
16200          TSA  2020  73.654518  LiteracyRate
16201          TSS  2020  65.858719  LiteracyRate
16209          UMC  2020  95.796822  LiteracyRate
16219          WLD  2020  86.682213  LiteracyRate
16228          AFG  2021  37.266041  LiteracyRate

[2542 rows x 4 columns]

In [242]:
Integrated_National_Indicators = HDI.append([AdjustedNetIncome2, CountryGdp2, DurSchoolCompulsory2, LifeExpectancy2, LiteracyRate2], ignore_index=True)
Integrated_National_Indicators

Country Code  Year      Value         Table
0              AFG  1990      0.302           HDI
1              ALB  1990       0.65           HDI
2              DZA  1990      0.572           HDI
3              ARG  1990      0.718           HDI
4              ARM  1990      0.654           HDI
...            ...   ...        ...           ...
50099          TSA  2020  73.654518  LiteracyRate
50100          TSS  2020  65.858719  LiteracyRate
50101          UMC  2020  95.796822  LiteracyRate
50102          WLD  2020  86.682213  LiteracyRate
50103          AFG  2021  37.266041  LiteracyRate

[50104 rows x 4 columns]

In [243]:
Integrated_National_Indicators.to_excel(r"Integrated_National_Indicators.xlsx")

In [244]:
Integrated_National_Indicators = Integrated_National_Indicators.astype({'Value':'float'})

In [245]:
period = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='HDI']['Year'].unique()
period

array(['1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997',
       '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005',
       '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013',
       '2014', '2015', '2016', '2017', '2018', '2019'], dtype=object)

In [246]:
table_name = Integrated_National_Indicators['Table'].unique()
table_name

array(['HDI', 'AdjustedNetIncome', 'CountryGdp', 'DurSchoolCompulsory',
       'LifeExpectancy', 'LiteracyRate'], dtype=object)

In [247]:
period[0]

'1990'

In [248]:
HDI_mean =[]
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='HDI']
    HDI_mean.append(x[x['Year']==i]['Value'].mean())
HDI_mean

[0.5996527777777778,
 0.6018541666666662,
 0.6041874999999998,
 0.6082291666666665,
 0.6123472222222224,
 0.6156689189189191,
 0.6210067567567569,
 0.6261824324324323,
 0.631445945945946,
 0.632317880794702,
 0.6327758620689652,
 0.6384022988505746,
 0.6441028571428573,
 0.6485965909090908,
 0.6553707865168538,
 0.6590324324324326,
 0.6664677419354843,
 0.6733655913978497,
 0.6795860215053763,
 0.683403225806452,
 0.6871968085106385,
 0.6927127659574466,
 0.6976755319148935,
 0.702643617021277,
 0.7067765957446809,
 0.7105106382978724,
 0.7133670212765959,
 0.7167830687830684,
 0.7194232804232806,
 0.7224232804232803]

In [249]:
AdjustedNetIncome_mean = []
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='AdjustedNetIncome']
    AdjustedNetIncome_mean.append(x[x['Year']==i]['Value'].mean())
AdjustedNetIncome_mean

[4019.2884275663823,
 4147.450178618287,
 4363.405697630764,
 4078.9211272438956,
 4223.2322024179775,
 4969.038817054864,
 5078.885225015858,
 5000.55353060298,
 4923.885723522019,
 4980.0309001440955,
 5064.411626531589,
 5017.184775201763,
 5239.962276671196,
 6042.064639466267,
 6933.7034051972705,
 7534.03621412397,
 8256.275337405534,
 9479.586816056268,
 10497.779882632747,
 9428.530268545624,
 10101.227599666643,
 11111.629247426432,
 10282.809885839184,
 10576.546748277806,
 10782.014718036644,
 9647.253116331654,
 9704.15125610883,
 10273.05608693268,
 10774.010878556865,
 10565.561456956235]

In [250]:
CountryGdp_mean = []
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='CountryGdp']
    CountryGdp_mean.append(x[x['Year']==i]['Value'].mean())
CountryGdp_mean


[753099291955.0869,
 775347033924.8702,
 822207600531.8431,
 827551936616.6509,
 884842971684.1018,
 953210126621.5823,
 982199496260.6471,
 981069487535.0543,
 970338036570.7848,
 993052565521.4856,
 1009753159610.7875,
 1002848950999.1044,
 1022642688486.9556,
 1153859722373.6865,
 1311851387323.046,
 1437490129114.0806,
 1572560291063.4043,
 1802193684647.3901,
 2005207339137.4714,
 1903765026649.2087,
 2102795734908.3513,
 2333965981851.0405,
 2404984937495.723,
 2482655526916.8267,
 2553925712595.809,
 2407635912800.568,
 2447650810544.06,
 2621669625083.7573,
 2787110601692.869,
 2864960118834.075]

In [251]:
DurSchoolCompulsory_mean = []
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='DurSchoolCompulsory']
    DurSchoolCompulsory_mean.append(x[x['Year']==i]['Value'].mean())
DurSchoolCompulsory_mean

[nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 8.566502463054187,
 8.657894736842104,
 8.755924170616113,
 8.85813953488372,
 8.930875576036867,
 8.95890410958904,
 9.037777777777778,
 9.092511013215859,
 9.16079295154185,
 9.220524017467248,
 9.275862068965518,
 9.32403433476395,
 9.390295358649789,
 9.497899159663865,
 9.594537815126051,
 9.69375,
 9.758333333333333,
 9.822314049586776,
 9.858024691358025,
 9.901234567901234,
 9.82857142857143,
 9.83265306122449]

In [252]:
LifeExpectancy_mean = []
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='LifeExpectancy']
    LifeExpectancy_mean.append(x[x['Year']==i]['Value'].mean())
LifeExpectancy_mean

[64.60147536554399,
 64.81877809631736,
 64.94646494135249,
 64.99072950450527,
 65.24937110863951,
 65.3876203012026,
 65.60292533200449,
 65.90851786835545,
 66.06299321518605,
 66.29231441764317,
 66.62802741876952,
 66.91793889294742,
 67.26694797106688,
 67.45796625104794,
 67.8379348117441,
 68.14323523429499,
 68.53686438731764,
 68.92091642417344,
 69.30769800377155,
 69.70338348813624,
 70.07686026660198,
 70.44798339967275,
 70.7991850657149,
 71.13085514281838,
 71.48316722070994,
 71.72506109452146,
 72.0079437347755,
 72.22680518669019,
 72.41957182863891,
 72.66266458777157]

In [253]:
LiteracyRate_mean = []
for i in period:
    x = Integrated_National_Indicators[Integrated_National_Indicators['Table']=='LiteracyRate']
    LiteracyRate_mean.append(x[x['Year']==i]['Value'].mean())
LiteracyRate_mean

[71.2360779502175,
 69.29446548031223,
 69.65891160356237,
 68.20014485647512,
 70.17790405423034,
 71.87008836534288,
 70.68620601965456,
 72.11146501053211,
 70.99188244861105,
 76.40257543447066,
 75.99691696166992,
 77.62677709034512,
 76.10503872370316,
 73.26608401078444,
 77.24001541733742,
 75.61377614544284,
 76.24419394783352,
 77.61027662377609,
 79.47413336264121,
 81.12260065851984,
 81.2810902438321,
 84.02132612286192,
 80.60361723058364,
 81.94207204182943,
 83.04998616969331,
 83.20228562531648,
 84.93415147964268,
 82.12069887433734,
 82.6485498327958,
 85.16368841355846]

In [269]:
pd.Series(HDI_mean).corr(pd.Series(AdjustedNetIncome_mean))

0.9557582233739411

In [270]:
pd.Series(HDI_mean).corr(pd.Series(CountryGdp_mean))

0.977890929347877

In [271]:
pd.Series(HDI_mean).corr(pd.Series(DurSchoolCompulsory_mean))

0.9906135118835231

In [272]:
pd.Series(HDI_mean).corr(pd.Series(LifeExpectancy_mean))

0.9976333105006102

In [273]:
pd.Series(HDI_mean).corr(pd.Series(LiteracyRate_mean))

0.9513113965285206

In [254]:
import altair as alt

In [255]:
df = Integrated_National_Indicators
df

Country Code  Year      Value         Table
0              AFG  1990   0.302000           HDI
1              ALB  1990   0.650000           HDI
2              DZA  1990   0.572000           HDI
3              ARG  1990   0.718000           HDI
4              ARM  1990   0.654000           HDI
...            ...   ...        ...           ...
50099          TSA  2020  73.654518  LiteracyRate
50100          TSS  2020  65.858719  LiteracyRate
50101          UMC  2020  95.796822  LiteracyRate
50102          WLD  2020  86.682213  LiteracyRate
50103          AFG  2021  37.266041  LiteracyRate

[50104 rows x 4 columns]

In [256]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [257]:
df['Table'].unique()

array(['HDI', 'AdjustedNetIncome', 'CountryGdp', 'DurSchoolCompulsory',
       'LifeExpectancy', 'LiteracyRate'], dtype=object)

In [258]:
country_code_list = sorted(df['Country Code'].unique())
input_dropdown = alt.binding_select(options=country_code_list,name='Select Country')
country_select = alt.selection_single(fields=['Country Code'],bind=input_dropdown,init={'Country Code':'DEU'})

In [259]:
chart_HDI = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "HDI"').properties(
  width=550,
  height=210,
  title = 'HDI'
)

In [260]:
chart_AdjustedNetIncome = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "AdjustedNetIncome"').properties(
  width=550,
  height=210,
  title = 'AdjustedNetIncome'
)

In [261]:
chart_CountryGdp = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "CountryGdp"').properties(
  width=550,
  height=210,
  title = 'CountryGdp'
)

In [262]:
chart_DurSchoolCompulsory = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "DurSchoolCompulsory"').properties(
  width=550,
  height=210,
  title = 'DurSchoolCompulsory'
)

In [263]:
chart_LifeExpectancy = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "LifeExpectancy"').properties(
  width=550,
  height=210,
  title = 'LifeExpectancy'
)

In [264]:
chart_LiteracyRate = alt.Chart().mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q')
    #color = 'Country Code'
).transform_filter(
  'datum.Table == "LiteracyRate"').properties(
  width=550,
  height=210,
  title = 'LiteracyRate'
)

In [265]:
chart = alt.vconcat((chart_HDI | chart_AdjustedNetIncome),(chart_CountryGdp | chart_DurSchoolCompulsory),(chart_LifeExpectancy | chart_LiteracyRate),data=df,
  title='Dashboard').add_selection(country_select).transform_filter(country_select).resolve_legend(
  color='independent'
)

In [266]:
chart

alt.VConcatChart(...)

In [267]:
chart.save('Die Zwei Fragezeichen.html')